In [3]:
# Dezinstalăm orice versiuni existente de Qiskit pentru a evita conflictele
!pip uninstall -y qiskit qiskit-terra qiskit-aer qiskit-ibmq-provider qiskit-ignis qiskit-aqua

# Instalăm cea mai recentă versiune de Qiskit și Qiskit IBM Runtime
!pip install qiskit qiskit_ibm_runtime --upgrade


Found existing installation: qiskit 1.2.0
Uninstalling qiskit-1.2.0:
  Successfully uninstalled qiskit-1.2.0
Found existing installation: qiskit-terra 0.23.3
Uninstalling qiskit-terra-0.23.3:
  Successfully uninstalled qiskit-terra-0.23.3
Found existing installation: qiskit-aer 0.12.0
Uninstalling qiskit-aer-0.12.0:
  Successfully uninstalled qiskit-aer-0.12.0
Found existing installation: qiskit-ibmq-provider 0.20.2
Uninstalling qiskit-ibmq-provider-0.20.2:
  Successfully uninstalled qiskit-ibmq-provider-0.20.2
  Using cached qiskit-1.2.0-cp38-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (12 kB)
Using cached qiskit-1.2.0-cp38-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (4.8 MB)


In [18]:
from qiskit import QuantumCircuit, QuantumRegister, ClassicalRegister, transpile
from qiskit_ibm_runtime import QiskitRuntimeService, Sampler, Session
import getpass
from statistics import mode
from collections import Counter
import numpy as np

# Funcție pentru a crea circuitul cuantic
def create_circuit(with_future_correction=False):
    qr = QuantumRegister(3, 'q')  # Registru cuantic cu 3 qubiți
    cr = ClassicalRegister(2, 'c')  # Registru clasic cu 2 biți
    qc = QuantumCircuit(qr, cr)  # Creăm circuitul cuantic

    # Aplicăm porțile cuantice
    qc.h(qr[0])  # Poarta Hadamard pe primul qubit
    qc.cx(qr[0], qr[1])  # Poarta CNOT între qubitul 0 și 1
    qc.s(qr[0])  # Poarta S pe primul qubit

    # Dacă este activată corecția viitorului, adăugăm o rotație condusă de măsurătoare
    if with_future_correction:
        qc.rx(np.pi/4, qr[0])  # Rotație RX pe qubitul 0

    qc.cx(qr[1], qr[2])  # Poarta CNOT între qubitul 1 și 2
    qc.h(qr[0])  # Poarta Hadamard din nou pe primul qubit

    # Măsurăm qubitul 0 și qubitul 2 în registrele clasice
    qc.measure(qr[0], cr[0])
    qc.measure(qr[2], cr[1])

    return qc

# Funcție pentru simulare și analiză
def simulate_and_analyze(backend, shots=1024, future_correction=False):
    qc = create_circuit(with_future_correction=future_correction)  # Creăm circuitul
    qc = transpile(qc, backend=backend)  # Transpilăm circuitul pentru a se potrivi cu backend-ul

    # Folosim sesiunea Qiskit Runtime pentru a rula sampler-ul
    with Session(backend=backend) as session:
        sampler = Sampler()
        job = sampler.run([qc], shots=shots)  # Trebuie să trecem circuitul într-o listă
        print(f"Job ID: {job.job_id()}. Așteptăm finalizarea jobului...")
        result = job.result()

        # Folosim metoda get_counts() pentru a obține un dicționar cu frecvențele rezultatelor
        pub_result = result._pub_results[0]
        data = pub_result.data
        counts = data.c.get_counts()  # Obținem dicționarul cu numărul de apariții al fiecărui bitstring

        # Transformăm numărătoarele în probabilități
        prob_00 = counts.get('00', 0) / shots
        prob_01 = counts.get('01', 0) / shots

    return prob_00, prob_01

# Funcție pentru a interpreta rezultatele
def interpret_result(prob_0_0, prob_0_1, threshold=0.15):
    # Interpretăm rezultatul bazat pe probabilități
    diff = abs(prob_0_0 - prob_0_1)
    ratio = prob_0_0 / (prob_0_1 + 1e-10)  # Evităm împărțirea la zero

    if diff <= threshold and 0.8 < ratio < 1.2:
        return '1'
    elif prob_0_0 > 0.4:
        return '0'
    else:
        return '1'

# Funcție pentru a trimite un bit și a determina rezultatul prin vot majoritar
def send_bit(bit, backend, repeats=3, future_correction=False):
    results = []
    for _ in range(repeats):
        prob_0_0, prob_0_1 = simulate_and_analyze(backend, future_correction=future_correction)
        received = interpret_result(prob_0_0, prob_0_1)
        results.append(received == bit)
    return mode(results)  # Returnăm rezultatul majoritar

# Funcție pentru a trimite un mesaj bit cu bit
def send_message(message, backend, future_correction=False):
    return [send_bit(bit, backend, future_correction=future_correction) for bit in message]

# Funcție pentru a converti rezultatele primite într-un mesaj
def receive_message(results):
    return ''.join('1' if result else '0' for result in results)

# Autentificare IBM Q
API_KEY = getpass.getpass('Introduceți cheia API IBM Q:')  # Introducem cheia API
QiskitRuntimeService.save_account(channel='ibm_quantum', token=API_KEY, overwrite=True)
service = QiskitRuntimeService(channel='ibm_quantum')

# Selectăm backend-ul cel mai puțin ocupat care are cel puțin 3 qubiți
backends = service.backends(filters=lambda b: b.configuration().n_qubits >= 3 and not b.configuration().simulator)
backend = min(backends, key=lambda b: b.status().pending_jobs)
print(f"Vom folosi dispozitivul: {backend.name}")

# Mesajul de 3 biți de transmis
message = "101"

print(f"Mesajul de transmis: {message}")

# Transmitem mesajul cu "corecție din viitor"
sent_results = send_message(message, backend, future_correction=True)
received_message = receive_message(sent_results)

# Afișăm rezultatele
print(f"\nMesaj trimis:    {message}")
print(f"Mesaj primit:    {received_message}")
print(f"Transmisie corectă: {message == received_message}")

# Detalii pentru fiecare bit
print("\nDetalii pentru fiecare bit:")
for i, bit in enumerate(message):
    prob_0_0, prob_0_1 = simulate_and_analyze(backend, future_correction=True)
    received = interpret_result(prob_0_0, prob_0_1)
    print(f"Bit {i}: Trimis {bit}, Primit {received}, "
          f"Prob(0,0): {prob_0_0:.4f}, Prob(0,1): {prob_0_1:.4f}, "
          f"Diferență: {abs(prob_0_0 - prob_0_1):.4f}, "
          f"Raport: {prob_0_0 / (prob_0_1 + 1e-10):.4f}")


Introduceți cheia API IBM Q:··········
Vom folosi dispozitivul: ibm_brisbane
Mesajul de transmis: 101
Job ID: cv9c8x3kfn8g008vsfqg. Așteptăm finalizarea jobului...
Job ID: cv9c96c8gpc0008gj120. Așteptăm finalizarea jobului...
Job ID: cv9c9fdsgfsg008ed3v0. Așteptăm finalizarea jobului...
Job ID: cv9c9rzemvv000852j50. Așteptăm finalizarea jobului...
Job ID: cv9casvemvv000852j6g. Așteptăm finalizarea jobului...
Job ID: cv9cb34sgfsg008ed420. Așteptăm finalizarea jobului...
Job ID: cv9cbcdm2bgg008kq0n0. Așteptăm finalizarea jobului...
Job ID: cv9cbp6m2bgg008kq0pg. Așteptăm finalizarea jobului...
Job ID: cv9ccqakfn8g008vsg20. Așteptăm finalizarea jobului...

Mesaj trimis:    101
Mesaj primit:    101
Transmisie corectă: True

Detalii pentru fiecare bit:
Job ID: cv9cd0m8gpc0008gj1j0. Așteptăm finalizarea jobului...
Bit 0: Trimis 1, Primit 1, Prob(0,0): 0.2637, Prob(0,1): 0.2617, Diferență: 0.0020, Raport: 1.0075
Job ID: cv9ce1gm2bgg008kq0z0. Așteptăm finalizarea jobului...
Bit 1: Trimis 0, Pri